# YOLOv3 Implementation for Pedestrian Detection

Written by Xuweiyi Chen & Jenny Rong

### Setup

In [1]:
#@title Mount your google drive
import os
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


Command to clone the repo if you have not yet cloned it to your google drive:
```
!git clone https://github.com/XuweiyiChen/Pedestrian_vehicles
```

In [2]:
#@title Get into the correct directory
%cd /content/gdrive/MyDrive/Pedestrian_vehicles/YOLO_v3_PyTorch

/content/gdrive/MyDrive/Pedestrian_vehicles/YOLO_v3_PyTorch


In [3]:
#@title Check working directory
%pwd

'/content/gdrive/MyDrive/Pedestrian_vehicles/YOLO_v3_PyTorch'

In [1]:
#@title Check the directory structre
#@markdown example structure is in README file
%ls

gdrive/  sample_data/


In [5]:
#@title Update albumentations package in order to run the file
!pip install --upgrade --force-reinstall --no-deps albumentations

  Using cached https://files.pythonhosted.org/packages/b0/be/3db3cd8af771988748f69eace42047d5edebf01eaa7e1293f3b3f75f989e/albumentations-1.0.0-py3-none-any.whl
  Found existing installation: albumentations 1.0.0
    Uninstalling albumentations-1.0.0:
      Successfully uninstalled albumentations-1.0.0


### Load Data

I have tried many different approaches in order to load the data into iCloud. Due to the fact the dataset I need to apply in order to make my model converge is very huge, there are many times I cannot fully load the data and labels perfectly. This is my final approches which brings the dataset into cloud and people can utilized the same approaches in order to make their customized change. 

This approaches is based on kaggle. For which this Kaggle approaches, people should have their own kaggle account and initilize their own API such as a *kaggle.json* file.

In [ ]:
#@title Step 1: Install Kaggle on Colab
!pip install -q kaggle

In [6]:
#@title Step 2: Upload *kaggle.json* to the Colab.
#@markdown get your kaggle.json file from kaggle
from google.colab import files
files.upload()

Saving kaggle.json to kaggle (1).json


{'kaggle.json': b'{"username":"jennyyyrong","key":"29dd22128c91e75581d61a97ec1e65ae"}'}

In [7]:
#@title Step 3: Make a directory and copy the identification file into the directory
%mkdir ~/.kaggle
%cp kaggle.json ~/.kaggle 

In [8]:
#@title Step 4: Connect kaggle using your *kaggle.json* file
!chmod 600 ~/.kaggle/kaggle.json

In [9]:
#@title Step 5: Make sure you can access kaggle right now
!kaggle datasets list

ref                                                         title                                              size  lastUpdated          downloadCount  
----------------------------------------------------------  ------------------------------------------------  -----  -------------------  -------------  
gpreda/reddit-vaccine-myths                                 Reddit Vaccine Myths                              229KB  2021-06-01 11:18:46           7041  
crowww/a-large-scale-fish-dataset                           A Large Scale Fish Dataset                          3GB  2021-04-28 17:03:01           4247  
imsparsh/musicnet-dataset                                   MusicNet Dataset                                   22GB  2021-02-18 14:12:19           1418  
dhruvildave/wikibooks-dataset                               Wikibooks Dataset                                   1GB  2021-02-18 10:08:27           2168  
mathurinache/twitter-edge-nodes                             Twitter Edge Nod

In [10]:
#@title Step 6: Download the kaggle dataset you want to use and unzip it
!kaggle datasets download -d aladdinpersson/pascal-voc-dataset-used-in-yolov3-video

pascal-voc-dataset-used-in-yolov3-video.zip: Skipping, found more recently modified local copy (use --force to force download)


In [ ]:
# unzip the file(takes a while)
# !unzip pascal-voc-dataset-used-in-yolov3-video.zip

### YOLO v3 Training

Step 1: Revise the config file *config.py* according to your own data.

Step 2: Run the trainning script.

In [11]:
#@title Train Script
import config
import torch
import torch.optim as optim

from model import YOLOv3
from tqdm import tqdm
from utils import (
    mean_average_precision,
    cells_to_bboxes,
    get_evaluation_bboxes,
    save_checkpoint,
    load_checkpoint,
    check_class_accuracy,
    get_loaders,
    plot_couple_examples
)
from loss import YoloLoss
import warnings
import matplotlib.pyplot as plt

warnings.filterwarnings("ignore")

torch.backends.cudnn.benchmark = True

all_losses = []

def train_fn(train_loader, model, optimizer, loss_fn, scaler, scaled_anchors):
    """
    This is how we train the model. This function utilized dataset.py,
    loss.py, model.py, and useful functions from utils.py in order to
    perform the training process.

    Calculating the total loss as the sum of the losses for each prediction
    scale, three of them in total. Utilize mixed precision training to train
    the model.

    Args:
        train_loader:
        model:
        optimizer:
        loss_fn:
        scaler:
        scaled_anchors:
    """
    loop = tqdm(train_loader, leave=True)
    losses = []
    for batch_idx, (x, y) in enumerate(loop):
        x = x.to(config.DEVICE)
        y0, y1, y2 = (
            y[0].to(config.DEVICE),
            y[1].to(config.DEVICE),
            y[2].to(config.DEVICE),
        )

        with torch.cuda.amp.autocast():
            out = model(x)
            loss = (
                    loss_fn(out[0], y0, scaled_anchors[0])
                    + loss_fn(out[1], y1, scaled_anchors[1])
                    + loss_fn(out[2], y2, scaled_anchors[2])
            )

        losses.append(loss.item())
        optimizer.zero_grad()
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()

        # update progress bar
        mean_loss = sum(losses) / len(losses)
        loop.set_postfix(loss=mean_loss)
        all_losses.append(mean_loss)

def main():
    """
    Setup the model, loss function, data loader. Run the train function
    for each epoch.

    We may want to consider tune the number for non max suppression and mean
    average precision in order to remove false positive. BY false positive, they
    are a set of wrong output boxes. We can get rid of them by increasing the
    parameters.
    """
    model = YOLOv3(num_classes=config.NUM_CLASSES).to(config.DEVICE)
    optimizer = optim.Adam(
        model.parameters(), lr=config.LEARNING_RATE, weight_decay=config.WEIGHT_DECAY
    )
    loss_fn = YoloLoss()
    scaler = torch.cuda.amp.GradScaler()

    train_loader, test_loader, train_eval_loader = get_loaders(
        train_csv_path=config.DATASET + "/train.csv", test_csv_path=config.DATASET + "/test.csv"
    )

    if config.LOAD_MODEL:
        load_checkpoint(
            config.CHECKPOINT_FILE, model, optimizer, config.LEARNING_RATE
        )

    scaled_anchors = (
            torch.tensor(config.ANCHORS)
            * torch.tensor(config.S).unsqueeze(1).unsqueeze(1).repeat(1, 3, 2)
    ).to(config.DEVICE)

    for epoch in range(config.NUM_EPOCHS):
        print('running epoch:', epoch)
        # plot_couple_examples(model, test_loader, 0.6, 0.5, scaled_anchors)
        train_fn(train_loader, model, optimizer, loss_fn, scaler, scaled_anchors)

        if config.SAVE_MODEL:
           save_checkpoint(model, optimizer, filename=f"checkpoint.pth.tar")

        # print(f"Currently epoch {epoch}")
        # print("On Train Eval loader:")
        # print("On Train loader:")
        # check_class_accuracy(model, train_loader, threshold=config.CONF_THRESHOLD)

        if epoch > 0 and epoch % 3 == 0:
            check_class_accuracy(model, test_loader, threshold=config.CONF_THRESHOLD)
            pred_boxes, true_boxes = get_evaluation_bboxes(
                test_loader,
                model,
                iou_threshold=config.NMS_IOU_THRESH,
                anchors=config.ANCHORS,
                threshold=config.CONF_THRESHOLD,
            )
            mapval = mean_average_precision(
                pred_boxes,
                true_boxes,
                iou_threshold=config.MAP_IOU_THRESH,
                box_format="midpoint",
                num_classes=config.NUM_CLASSES,
            )
            print(f"MAP: {mapval.item()}")
            model.train()
    plt.plot(all_losses)

/usr/local/lib/python3.7/dist-packages/albumentations/imgaug/transforms.py:337: FutureWarning: This IAAAffine is deprecated. Please use Affine instead
  warnings.warn("This IAAAffine is deprecated. Please use Affine instead", FutureWarning)


In [65]:
#@title Run Train Script
main()



  0%|          | 0/1104 [00:00<?, ?it/s]

running epoch: 0
__________________________________
tensor(5.9078, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.0957, device='cuda:0', grad_fn=<MulBackward0>)
tensor(7.0206, device='cuda:0', grad_fn=<MulBackward0>)
tensor(3.4003, device='cuda:0', grad_fn=<MulBackward0>)


__________________________________
tensor(6.5696, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.1361, device='cuda:0', grad_fn=<MulBackward0>)
tensor(7.1691, device='cuda:0', grad_fn=<MulBackward0>)
tensor(3.0779, device='cuda:0', grad_fn=<MulBackward0>)


__________________________________
tensor(9.4469, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.1864, device='cuda:0', grad_fn=<MulBackward0>)
tensor(7.0138, device='cuda:0', grad_fn=<MulBackward0>)
tensor(3.3180, device='cuda:0', grad_fn=<MulBackward0>)






  0%|          | 0/1104 [00:01<?, ?it/s, loss=53.3]

  0%|          | 1/1104 [00:01<24:13,  1.32s/it, loss=53.3]

__________________________________
tensor(3.4627, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.0656, device='cuda:0', grad_fn=<MulBackward0>)
tensor(6.9989, device='cuda:0', grad_fn=<MulBackward0>)
tensor(3.2715, device='cuda:0', grad_fn=<MulBackward0>)


__________________________________
tensor(5.9838, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.0916, device='cuda:0', grad_fn=<MulBackward0>)
tensor(7.1459, device='cuda:0', grad_fn=<MulBackward0>)
tensor(2.9265, device='cuda:0', grad_fn=<MulBackward0>)


__________________________________
tensor(12.3317, device='cuda:0', grad_fn=<MulBackward0>)
tensor(0.2373, device='cuda:0', grad_fn=<MulBackward0>)
tensor(7.0257, device='cuda:0', grad_fn=<MulBackward0>)
tensor(3.0618, device='cuda:0', grad_fn=<MulBackward0>)






  0%|          | 1/1104 [00:01<24:13,  1.32s/it, loss=53]  

  0%|          | 2/1104 [00:01<19:09,  1.04s/it, loss=53]

...

100%|██████████| 1104/1104 [07:33<00:00,  2.44it/s, loss=14.9]


=> Saving checkpoint




  0%|          | 0/1104 [00:00<?, ?it/s]

running epoch: 3


RuntimeError: ignored

### Detection Demo

In [12]:
#@title Detection
import config
import torch
import torch.optim as optim

from model import YOLOv3
from utils import (load_checkpoint, check_class_accuracy, get_loaders, plot_couple_examples)

def detect():
    """
    Load the model from the trained checkpoints.
    """
    model = YOLOv3(num_classes=config.NUM_CLASSES).to(config.DEVICE)
    optimizer = optim.Adam(
        model.parameters(), lr=config.LEARNING_RATE, weight_decay=config.WEIGHT_DECAY
    )

    train_loader, test_loader, train_eval_loader = get_loaders(
        train_csv_path=config.DATASET + "/2examples.csv", test_csv_path=config.DATASET + "/2examples.csv"
    )

    load_checkpoint('checkpoint.pth.tar', model, optimizer, config.LEARNING_RATE)

    scaled_anchors = (
            torch.tensor(config.ANCHORS)
            * torch.tensor(config.S).unsqueeze(1).unsqueeze(1).repeat(1, 3, 2)
    ).to(config.DEVICE)

    plot_couple_examples(model, test_loader, 0.6, 0.5, scaled_anchors)

In [1]:
#@title Run Detection Demo
detect()